In [1]:
print("Test")

Test


In [2]:
%pwd

'c:\\Users\\daksh.DAKSH-XPS\\OneDrive\\Desktop\\Software Projects\\VectorQuery\\research'

In [3]:
import os
os.chdir("../")

In [4]:
%pwd

'c:\\Users\\daksh.DAKSH-XPS\\OneDrive\\Desktop\\Software Projects\\VectorQuery'

In [5]:
from langchain.document_loaders import PyPDFLoader, DirectoryLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter

In [7]:
# Extracting the text from PDF files

def load_pdf_files(data):
    loader = DirectoryLoader(
        data,
        glob="*.pdf",
        loader_cls=PyPDFLoader
    )

    documents = loader.load()
    return documents

In [8]:
extracted_data = load_pdf_files("data")

In [9]:
extracted_data

[Document(metadata={'producer': 'PyPDF', 'creator': 'HELIOS pdfcat', 'creationdate': '2012-12-14T17:00:05+05:30', 'moddate': '2013-03-21T13:46:29-04:00', 'title': 'Fundamentals of Thermodynamics, 8th Edition', 'ebx_publisher': '/WILEY TextBooks', 'author': 'Claus Borgnakke', 'source': 'data\\Applied Thermodynamics.pdf', 'total_pages': 916, 'page': 0, 'page_label': 'C-1'}, page_content='Fundamentals of  \nThermodynamics\nBORGNAKKE t SONNTAG\n8e'),
 Document(metadata={'producer': 'PyPDF', 'creator': 'HELIOS pdfcat', 'creationdate': '2012-12-14T17:00:05+05:30', 'moddate': '2013-03-21T13:46:29-04:00', 'title': 'Fundamentals of Thermodynamics, 8th Edition', 'ebx_publisher': '/WILEY TextBooks', 'author': 'Claus Borgnakke', 'source': 'data\\Applied Thermodynamics.pdf', 'total_pages': 916, 'page': 1, 'page_label': 'C-2'}, page_content='P1: PCX/OVY P2: PCX/OVY QC: PCX/OVY T1: PCX\nWB00776-FM JWCL672-Borgnakke-v1 October 25, 2012 17:24\nxviii\nThis page is intentionally left blank'),
 Document(m

In [10]:
len(extracted_data)

916

In [14]:
from typing import List
from langchain.schema import Document

# With a list of document objects, this function will return a new list of document objects containing only the source and page_content data.
def filter_doc(docs: List[Document]) -> List[Document]:
    minimal_doc: List[Document] = []
    for doc in docs:
        src = doc.metadata.get("source")
        minimal_doc.append(
            Document(
                page_content=doc.page_content,
                metadata={"source": src}
            )
        )
    
    return minimal_doc

In [15]:
minimal_doc = filter_doc(extracted_data)

In [16]:
minimal_doc

[Document(metadata={'source': 'data\\Applied Thermodynamics.pdf'}, page_content='Fundamentals of  \nThermodynamics\nBORGNAKKE t SONNTAG\n8e'),
 Document(metadata={'source': 'data\\Applied Thermodynamics.pdf'}, page_content='P1: PCX/OVY P2: PCX/OVY QC: PCX/OVY T1: PCX\nWB00776-FM JWCL672-Borgnakke-v1 October 25, 2012 17:24\nxviii\nThis page is intentionally left blank'),
 Document(metadata={'source': 'data\\Applied Thermodynamics.pdf'}, page_content='P1: PCX/OVY P2: PCX/OVY QC: PCX/OVY T1: PCX\nWB00776-IFC JWCL672-Borgnakke-v1 October 1, 2012 19:20\nFundamental Physical Constants\nAvogadro N0 = 6.022 1415 × 1023 mol−1\nBoltzmann k = 1.380 6505 × 10−23 JK −1\nPlanck h = 6.626 0693 × 10−34 Js\nGas Constant R = N0 k = 8.314 472 J mol−1 K−1\nAtomic Mass Unit m 0 = 1.660 538 86× 10−27 kg\nVelocity of light c = 2.997 924 58× 108 ms−1\nElectron Charge e = 1.602 176 53× 10−19 C\nElectron Mass m e = 9.109 3826 × 10−31 kg\nProton Mass m p = 1.672 621 71× 10−27 kg\nGravitation (Std.) g = 9.806 65 

In [17]:
# This function will perform chunking; splitting the text content into smaller chunks.

def text_split(minimal_doc):
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size = 500,
        chunk_overlap = 20
    )

    chunk_text = text_splitter.split_documents(minimal_doc)
    return chunk_text

In [18]:
chunk_text = text_split(minimal_doc)
print(f"Number of chunks: {len(chunk_text)}")

Number of chunks: 5290


In [ ]:
# Now, the chunks must be passed into an embedding model so that each chunk has a corresponding vector embedding.
# First, I will download and return the HuggingFace embedding model so it can be used to create the embeddings.

from langchain_huggingface import HuggingFaceEmbeddings

def embedding_model():
    model_name ="sentence-transformers/all-MiniLM-L6-v2" # This model name was obtained from the HuggingFace website.
    embeddings = HuggingFaceEmbeddings(
        model_name = model_name # Setting the model_name value in the HuggingFaceEmbeddings function to the model_name that I obtained above.
    )
    return embeddings

embedding = embedding_model() # Calling the function which downloads and returns the embedding model.

C:\Users\daksh.DAKSH-XPS\AppData\Local\Temp\ipykernel_33064\464795025.py:8: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-huggingface package and should be used instead. To use it run `pip install -U :class:`~langchain-huggingface` and import as `from :class:`~langchain_huggingface import HuggingFaceEmbeddings``.
  embeddings = HuggingFaceEmbeddings(
c:\Users\daksh.DAKSH-XPS\anaconda3\envs\vectorquery\Lib\site-packages\huggingface_hub\file_download.py:143: UserWarning: `huggingface_hub` cache-system uses symlinks by default to efficiently store duplicated files but your machine does not support them in C:\Users\daksh.DAKSH-XPS\.cache\huggingface\hub\models--sentence-transformers--all-MiniLM-L6-v2. Caching files will still work but in a degraded version that might require more space on your disk. This warning can be disabled by setting the `HF_H